In [1]:
import numpy as np
import h5py
import glob
import os
from pycbc import pnutils
from pycbc import catalog

from pycbc.inference.io import loadfile
from pycbc.workflow import WorkflowConfigParser
from pycbc import cosmology

# Read in the 57 GW events from config file and write data file

In [2]:
file = glob.glob('./3ogc_github_config/*.ini')

name = []
for f in file:
    name.append(f.split('-')[1][:15])
    
name.sort()

In [3]:
name.remove('gw190521_030229')
name.remove('gw190521_030229')
name.remove('gw170817_124104')
name.remove('gw190425_081805')

In [4]:
for n in name:
    if n == 'gw190521_030229' or n== 'gw170817_124104' or n=='gw190425_081805':
        pass
    else:
        file = glob.glob('./3ogc_github_config/*'+n+'*.ini')
        basename = os.path.basename(file[0])
        cp = WorkflowConfigParser([file[0]])
        print(basename,cp.get('data', 'instruments'),cp.get('data','trigger-time'))
        det = cp.get('data', 'instruments')
        os.remove('./data_config_file_3ogc/data-'+basename.split('-')[1])
        with open('./data_config_file_3ogc/data-'+basename.split('-')[1], 'w') as t:
            t.write('[data]\n')
            t.write('instruments =' +cp.get('data', 'instruments')+ '\n')
            t.write('trigger-time =' +cp.get('data', 'trigger-time')+ '\n')
            # try to write frame-files or frame-type
            if cp.has_option('data','frame-files'):
                t.write('frame-files =' +cp.get('data', 'frame-files')+ '\n')
            elif cp.has_option('data','frame-type'):
                t.write('frame-type =' +cp.get('data', 'frame-type')+ '\n')
                
            t.write('channel-name =' +cp.get('data', 'channel-name')+ '\n')
            t.write('analysis-start-time = -4\n')
            t.write('analysis-end-time = 4\n')
            if det == 'H1 L1 V1' or det == 'H1 V1 L1':
                t.write('data-conditioning-low-freq = H1:0 L1:0 V1:0\n')
            elif det == 'H1 L1':
                t.write('data-conditioning-low-freq = H1:0 L1:0\n')
            elif det == 'H1 L1':
                t.write('data-conditioning-low-freq = H1:0 L1:0 V1:0\n')
            elif det == 'L1 V1':
                t.write('data-conditioning-low-freq = L1:0 V1:0\n')
            elif det == 'H1 V1':
                t.write('data-conditioning-low-freq = H1:0 V1:0\n')
            elif det == 'L1':
                t.write('data-conditioning-low-freq = H1:0 V1:0\n')
            else:
                print('Warn:This event does not belong to any instrument combinations!!!')
            t.write('psd-estimation =' +cp.get('data', 'psd-estimation')+ '\n')
            t.write('psd-start-time =' +cp.get('data', 'psd-start-time')+ '\n')
            t.write('psd-end-time =' +cp.get('data', 'psd-end-time')+ '\n')
            t.write('psd-inverse-length =' +cp.get('data', 'psd-inverse-length')+ '\n')
            t.write('psd-segment-length =' +cp.get('data', 'psd-segment-length')+ '\n')
            t.write('psd-segment-stride =' +cp.get('data', 'psd-segment-stride')+ '\n')
            t.write('sample-rate =' +cp.get('data', 'sample-rate')+ '\n')
            t.write('strain-high-pass = 10\n')
            t.write('pad-data =' +cp.get('data', 'pad-data')+ '\n')

inference-gw150914_095045.ini H1 L1 1126259462.43
inference-gw151012_095443.ini H1 L1 1128678900.45
inference-gw151226_033853.ini H1 L1 1135136350.65
inference-gw170104_101158.ini H1 L1 V1 1167559936.60
inference-gw170121_212536.ini H1 L1 V1 1169069154.58
inference-gw170202_135657.ini H1 L1 V1 1170079035.73
inference-gw170304_163753.ini H1 L1 V1 1172680691.37
inference-gw170403_230611.ini H1 L1 V1 1175295989.23
inference-gw170608_020116.ini H1 L1 1180922494.49
inference-gw170727_010430.ini H1 L1 V1 1185152688.03
inference-gw170729_185629.ini H1 L1 V1 1185389807.33
inference-gw170809_082821.ini H1 L1 V1 1186302519.76
inference-gw170814_103043.ini H1 L1 V1 1186741861.53
inference-gw170818_022509.ini H1 L1 V1 1187058327.09
inference-gw170823_131358.ini H1 L1 V1 1187529256.52
inference-gw190408_181802.ini H1 L1 V1 1238782700.3
inference-gw190412_053044.ini H1 L1 V1 1239082262.2
inference-gw190413_052954.ini H1 L1 V1 1239168612.5
inference-gw190413_134308.ini H1 L1 V1 1239198206.7
inference

# Generating events.ini from reading posterior files

In [5]:
def info(name):
    print(name)
    h5file = glob.glob('/work/yifan.wang/3ogcPE/datarelease/allposterior/*'+str(name)+'*.hdf')
    print(h5file)
    f = h5py.File(h5file[0],'r')
    print(f['samples'].keys())
    # ra, dec, mass, t
    i = np.argmax(f['samples']['loglikelihood'][:])
    ra = f['samples']['ra'][i]
    dec = f['samples']['dec'][i]
    mtotal = f['samples']['srcmass1'][i]+f['samples']['srcmass2'][i] * (f['samples']['redshift'][i]+1)
    t = f.attrs['trigger_time'] + f['samples']['delta_tc'][i]
    final_freq = pnutils.get_final_freq('SEOBNRv4',f['samples']['srcmass1'][i]* (f['samples']['redshift'][i]+1),\
                                        f['samples']['srcmass2'][i]* (f['samples']['redshift'][i]+1),\
                                        0,0)
    f.close()
    return ra,dec,mtotal,np.median(final_freq),t

In [6]:
os.remove('events.ini')
with open('events.ini', 'w') as t:
    for n in name:
        print(n)
        datafile = glob.glob('./data_config_file_3ogc/*'+str(n)+'*.ini')[0]
        t.write('[event-'+str(n)+']\n')
        t.write('label='+str(n)+'\n')
        t.write('config-files='+str(datafile)+'\n')
        t.write('\t\t\tkerr_base.ini\n')
        # need ra,dec,final_mass
        ra,dec,mtotal,final_freq,time = info(n[2:])
        t.write('config-overrides =static_params:ra:'+str(ra)+'\n')
        t.write('\t\t\tstatic_params:dec:'+str(dec)+'\n')
        t.write('\t\t\tdata:trigger-time:'+str(time)+'\n')
        if mtotal < 150:
            t.write('\t\t\tprior-final_mass:min-final_mass:10\n')
            t.write('\t\t\tprior-final_mass:max-final_mass:200\n')
        else:
            t.write('\t\t\tprior-final_mass:min-final_mass:100\n')
            t.write('\t\t\tprior-final_mass:max-final_mass:500\n')
        if final_freq > 1024:
            t.write('\t\t\tdata:sample-rate:4096\n')
        t.write('\n')
t.close()

gw150914_095045
150914_095045
['/work/yifan.wang/3ogcPE/datarelease/allposterior/GW150914_095045-PYCBC-POSTERIOR-XPHM.hdf']
<KeysViewHDF5 ['chi_eff', 'chi_p', 'coa_phase', 'dec', 'delta_tc', 'distance', 'inclination', 'loglikelihood', 'logwt', 'q', 'ra', 'redshift', 'spin1_a', 'spin1_azimuthal', 'spin1_polar', 'spin2_a', 'spin2_azimuthal', 'spin2_polar', 'srcmass1', 'srcmass2', 'srcmchirp', 'srcmtot']>
gw151012_095443
151012_095443
['/work/yifan.wang/3ogcPE/datarelease/allposterior/GW151012_095443-PYCBC-POSTERIOR-XPHM.hdf']
<KeysViewHDF5 ['chi_eff', 'chi_p', 'coa_phase', 'dec', 'delta_tc', 'distance', 'inclination', 'loglikelihood', 'logwt', 'q', 'ra', 'redshift', 'spin1_a', 'spin1_azimuthal', 'spin1_polar', 'spin2_a', 'spin2_azimuthal', 'spin2_polar', 'srcmass1', 'srcmass2', 'srcmchirp', 'srcmtot']>
gw151226_033853
151226_033853
['/work/yifan.wang/3ogcPE/datarelease/allposterior/GW151226_033853-PYCBC-POSTERIOR-XPHM.hdf']
<KeysViewHDF5 ['chi_eff', 'chi_p', 'coa_phase', 'dec', 'delta_tc

gw190513_205428
190513_205428
['/work/yifan.wang/3ogcPE/datarelease/allposterior/GW190513_205428-PYCBC-POSTERIOR-XPHM.hdf']
<KeysViewHDF5 ['chi_eff', 'chi_p', 'coa_phase', 'dec', 'delta_tc', 'distance', 'inclination', 'loglikelihood', 'logwt', 'q', 'ra', 'redshift', 'spin1_a', 'spin1_azimuthal', 'spin1_polar', 'spin2_a', 'spin2_azimuthal', 'spin2_polar', 'srcmass1', 'srcmass2', 'srcmchirp']>
gw190514_065416
190514_065416
['/work/yifan.wang/3ogcPE/datarelease/allposterior/GW190514_065416-PYCBC-POSTERIOR-XPHM.hdf']
<KeysViewHDF5 ['chi_eff', 'chi_p', 'coa_phase', 'dec', 'delta_tc', 'distance', 'inclination', 'loglikelihood', 'logwt', 'q', 'ra', 'redshift', 'spin1_a', 'spin1_azimuthal', 'spin1_polar', 'spin2_a', 'spin2_azimuthal', 'spin2_polar', 'srcmass1', 'srcmass2', 'srcmchirp']>
gw190517_055101
190517_055101
['/work/yifan.wang/3ogcPE/datarelease/allposterior/GW190517_055101-PYCBC-POSTERIOR-XPHM.hdf']
<KeysViewHDF5 ['chi_eff', 'chi_p', 'coa_phase', 'dec', 'delta_tc', 'distance', 'inclin

<KeysViewHDF5 ['chi_eff', 'chi_p', 'coa_phase', 'dec', 'delta_tc', 'distance', 'inclination', 'loglikelihood', 'logwt', 'q', 'ra', 'redshift', 'spin1_a', 'spin1_azimuthal', 'spin1_polar', 'spin2_a', 'spin2_azimuthal', 'spin2_polar', 'srcmass1', 'srcmass2', 'srcmchirp', 'srcmtot']>
gw190828_065509
190828_065509
['/work/yifan.wang/3ogcPE/datarelease/allposterior/GW190828_065509-PYCBC-POSTERIOR-XPHM.hdf']
<KeysViewHDF5 ['chi_eff', 'chi_p', 'coa_phase', 'dec', 'delta_tc', 'distance', 'inclination', 'loglikelihood', 'logwt', 'q', 'ra', 'redshift', 'spin1_a', 'spin1_azimuthal', 'spin1_polar', 'spin2_a', 'spin2_azimuthal', 'spin2_polar', 'srcmass1', 'srcmass2', 'srcmchirp', 'srcmtot']>
gw190910_112807
190910_112807
['/work/yifan.wang/3ogcPE/datarelease/allposterior/GW190910_112807-PYCBC-POSTERIOR-XPHM.hdf']
<KeysViewHDF5 ['chi_eff', 'chi_p', 'coa_phase', 'dec', 'delta_tc', 'distance', 'inclination', 'loglikelihood', 'logwt', 'q', 'ra', 'redshift', 'spin1_a', 'spin1_azimuthal', 'spin1_polar', 